In [1]:
import io
import os
import json
from enum import Enum

# Imports the Google Cloud client library
from google.oauth2 import service_account
from google.cloud import vision
from google.cloud.vision import types
from PIL import Image, ImageDraw

# Use credentials for google client
credentials = service_account.Credentials.from_service_account_file('credentials.json')
client = vision.ImageAnnotatorClient(credentials=credentials)

In [9]:
class FeatureType(Enum):
    PAGE = 1
    BLOCK = 2
    PARA = 3
    WORD = 4
    SYMBOL = 5


def draw_boxes(image, bounds, color):
    """Draw a border around the image using the hints in the vector list."""
    # [START draw_blocks]
    draw = ImageDraw.Draw(image)

    for bound in bounds:
        draw.polygon([
            bound.vertices[0].x, bound.vertices[0].y,
            bound.vertices[1].x, bound.vertices[1].y,
            bound.vertices[2].x, bound.vertices[2].y,
            bound.vertices[3].x, bound.vertices[3].y], None, color)
    return image
    # [END draw_blocks]


def get_document_bounds(image_file, feature):
    # [START detect_bounds]
    """Returns document bounds given an image."""
    
    bounds = []

    with io.open(image_file, 'rb') as image_file:
        content = image_file.read()

    image = types.Image(content=content)

    response = client.document_text_detection(image=image)
    document = response.full_text_annotation
    print(response)
    # Collect specified feature bounds by enumerating all document features
    for page in document.pages:
        for block in page.blocks:
            for paragraph in block.paragraphs:
                for word in paragraph.words:
                    for symbol in word.symbols:
                        if (feature == FeatureType.SYMBOL):
                            bounds.append(symbol.bounding_box)

                    if (feature == FeatureType.WORD):
                        bounds.append(word.bounding_box)

                if (feature == FeatureType.PARA):
                    bounds.append(paragraph.bounding_box)

            if (feature == FeatureType.BLOCK):
                bounds.append(block.bounding_box)

        if (feature == FeatureType.PAGE):
            bounds.append(block.bounding_box)

    # The list `bounds` contains the coordinates of the bounding boxes.
    # [END detect_bounds]
    return bounds

def render_doc_text(filein, fileout):
    # [START render_doc_text]
    image = Image.open(filein)
    image.show()
    bounds = get_document_bounds(filein, FeatureType.PAGE)
    draw_boxes(image, bounds, 'blue')
    bounds = get_document_bounds(filein, FeatureType.PARA)
    draw_boxes(image, bounds, 'red')
    bounds = get_document_bounds(filein, FeatureType.WORD)
    draw_boxes(image, bounds, 'yellow')
    
    if fileout is not 0:
        image.save(fileout)
    image.show()

In [10]:
render_doc_text('med2.jpg', 'test.jpg')

text_annotations {
  locale: "en"
  description: "INorth Shore\nA Fast & Easy\nQUICK PAY\nUniversity Health System\nPO BOX 0000 | ANYWHERE USA 12345-0000\nHospital/Clinic Statement\nAPEX341\nNo Login Required!\ni For help with billing questions, please call:\n(555) 555-5555 or (555) 555-5556\nMonday - Friday, 8:00am \342\200\223 5:30pm\nO Check if address/insurance changes are on back\nAddressee\nO Pay Online: northshore.mysecurebill.com\nAccount Number\nDue Date\nAmount Due Amount Paid\n654321\n11/10/2014\n$500.00\nPlease make checks payable and remit to:\nPage 1\nJON Q DOE\n1234 MAIN ST\nALBERT LEA, USA 56007\nYOUR FACILITY\nPO BOX 0000\nANYWHERE USA 12345-0000\nX0000000654321 11102014 000100000 2\nmyEasyMatch Code: A-BCDEF-000000-GHIJKL\nAccount Number\nPlease detach and return top portion with payment.\nStatement Date\nDue Date\nAccount Name\n654321\nJon Q. Doe\n10/21/2014\n11/10/2014\nStatus\nCharges\nPayments/\nAdjustments\nPatient\nBalance\n$500.00\n-$250.00\nCurrent\n$250.00\nD

text_annotations {
  locale: "en"
  description: "INorth Shore\nA Fast & Easy\nQUICK PAY\nUniversity Health System\nPO BOX 0000 | ANYWHERE USA 12345-0000\nHospital/Clinic Statement\nAPEX341\nNo Login Required!\ni For help with billing questions, please call:\n(555) 555-5555 or (555) 555-5556\nMonday - Friday, 8:00am \342\200\223 5:30pm\nO Check if address/insurance changes are on back\nAddressee\nO Pay Online: northshore.mysecurebill.com\nAccount Number\nDue Date\nAmount Due Amount Paid\n654321\n11/10/2014\n$500.00\nPlease make checks payable and remit to:\nPage 1\nJON Q DOE\n1234 MAIN ST\nALBERT LEA, USA 56007\nYOUR FACILITY\nPO BOX 0000\nANYWHERE USA 12345-0000\nX0000000654321 11102014 000100000 2\nmyEasyMatch Code: A-BCDEF-000000-GHIJKL\nAccount Number\nPlease detach and return top portion with payment.\nStatement Date\nDue Date\nAccount Name\n654321\nJon Q. Doe\n10/21/2014\n11/10/2014\nStatus\nCharges\nPayments/\nAdjustments\nPatient\nBalance\n$500.00\n-$250.00\nCurrent\n$250.00\nD

text_annotations {
  locale: "en"
  description: "INorth Shore\nA Fast & Easy\nQUICK PAY\nUniversity Health System\nPO BOX 0000 | ANYWHERE USA 12345-0000\nHospital/Clinic Statement\nAPEX341\nNo Login Required!\ni For help with billing questions, please call:\n(555) 555-5555 or (555) 555-5556\nMonday - Friday, 8:00am \342\200\223 5:30pm\nO Check if address/insurance changes are on back\nAddressee\nO Pay Online: northshore.mysecurebill.com\nAccount Number\nDue Date\nAmount Due Amount Paid\n654321\n11/10/2014\n$500.00\nPlease make checks payable and remit to:\nPage 1\nJON Q DOE\n1234 MAIN ST\nALBERT LEA, USA 56007\nYOUR FACILITY\nPO BOX 0000\nANYWHERE USA 12345-0000\nX0000000654321 11102014 000100000 2\nmyEasyMatch Code: A-BCDEF-000000-GHIJKL\nAccount Number\nPlease detach and return top portion with payment.\nStatement Date\nDue Date\nAccount Name\n654321\nJon Q. Doe\n10/21/2014\n11/10/2014\nStatus\nCharges\nPayments/\nAdjustments\nPatient\nBalance\n$500.00\n-$250.00\nCurrent\n$250.00\nD